# EnergyPlus Simulation Results Visualization

This notebook plots the results from the external controller simulation.
- **Temperatures**: Outdoor and zone temperatures
- **Energy Consumption**: Total facility power
- **Control Actions**: Heating and cooling setpoints

In [8]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from datetime import datetime, timedelta
import os

## Load Simulation Data

In [9]:
# Load the simulation log
csv_path = 'outputs/external_control/simulation_log.csv'
df = pd.read_csv(csv_path)

# Display basic info
print(f"Loaded {len(df)} timesteps")
print(f"Columns: {list(df.columns)}")
df.head()

Loaded 2016 timesteps
Columns: ['timestamp', 'datetime', 'timestep', 'outdoor_temp_C', 'total_power_W', 'cooling_setpoint_C', 'heating_setpoint_C', 'zone_temp_Core_bottom_C', 'zone_temp_Core_mid_C', 'zone_temp_Core_top_C', 'zone_temp_Perimeter_bot_ZN_1_C', 'zone_temp_Perimeter_bot_ZN_2_C', 'zone_temp_Perimeter_bot_ZN_3_C', 'zone_temp_Perimeter_bot_ZN_4_C', 'zone_temp_Perimeter_mid_ZN_1_C', 'zone_temp_Perimeter_mid_ZN_2_C', 'zone_temp_Perimeter_mid_ZN_3_C', 'zone_temp_Perimeter_mid_ZN_4_C', 'zone_temp_Perimeter_top_ZN_1_C', 'zone_temp_Perimeter_top_ZN_2_C', 'zone_temp_Perimeter_top_ZN_3_C', 'zone_temp_Perimeter_top_ZN_4_C']


timestamp             datetime  timestep  outdoor_temp_C  \
0  2024-07-01T00:11:00  2024-07-01 00:11:00         1            26.5   
1  2024-07-01T00:17:00  2024-07-01 00:17:00         2            26.5   
2  2024-07-01T00:22:00  2024-07-01 00:22:00         3            26.5   
3  2024-07-01T00:28:00  2024-07-01 00:28:00         4            26.5   
4  2024-07-01T00:30:00  2024-07-01 00:30:00         5            26.5   

   total_power_W  cooling_setpoint_C  heating_setpoint_C  \
0   3.128884e+07                24.0                21.0   
1   3.102345e+07                25.0                20.0   
2   2.218785e+07                25.0                20.0   
3   1.635545e+07                25.0                20.0   
4   1.367186e+07                25.0                20.0   

   zone_temp_Core_bottom_C  zone_temp_Core_mid_C  zone_temp_Core_top_C  ...  \
0                25.609356             25.738798             26.109053  ...   
1                25.435471             25.601887             25.887322  ...   
2                25.059722             25.217186             25.107700  ...   
3                25.000973             24.966081             25.000419  ...   
4                24.999726             24.997104             24.998432  ...   

   zone_temp_Perimeter_bot_ZN_3_C  zone_temp_Perimeter_bot_ZN_4_C  \
0                       25.773851                       25.954337   
1                       25.605020                       25.600847   
2                       25.120369                       25.053823   
3                       25.002415                       25.000681   
4                       24.999044                       24.998500   

   zone_temp_Perimeter_mid_ZN_1_C  zone_temp_Perimeter_mid_ZN_2_C  \
0                       25.963243                       25.532766   
1                       25.677807                       25.201257   
2                       25.123238                       25.012212   
3                       25.002441                       24.999105   
4                       24.998615                       24.998533   

   zone_temp_Perimeter_mid_ZN_3_C  zone_temp_Perimeter_mid_ZN_4_C  \
0                       26.093117                       25.747060   
1                       25.877413                       25.331505   
2                       25.327087                       25.016477   
3                       25.038019                       24.999117   
4                       24.998840                       24.998365   

   zone_temp_Perimeter_top_ZN_1_C  zone_temp_Perimeter_top_ZN_2_C  \
0                       25.888685                       25.523656   
1                       25.547098                       25.180038   
2                       25.005385                       25.000864   
3                       24.999053                       24.998855   
4                       24.998347                       24.998376   

   zone_temp_Perimeter_top_ZN_3_C  zone_temp_Perimeter_top_ZN_4_C  
0                       26.033948                       25.540313  
1                       25.754664                       25.190729  
2                       25.011696                       25.001187  
3                       24.999284                       24.998760  
4                       24.998345                       24.998278  

[5 rows x 22 columns]

## Configure Simulation Parameters

In [10]:
# The CSV now includes datetime from the simulation (from weather file year)
# Parse the datetime column directly
if 'datetime' in df.columns:
    df['datetime'] = pd.to_datetime(df['datetime'])
    df.set_index('datetime', inplace=True)
    print(f"Using datetime from simulation")
else:
    # Fallback: construct datetime from individual columns if available
    if 'year' in df.columns:
        df['datetime'] = pd.to_datetime(df[['year', 'month', 'day', 'hour', 'minute']].assign(second=0))
        df.set_index('datetime', inplace=True)
        print(f"Constructed datetime from year/month/day/hour/minute columns")
    else:
        # Legacy fallback: manual construction
        TIMESTEPS_PER_HOUR = 12
        START_DATE = datetime(2007, 1, 1)
        df['datetime'] = [START_DATE + timedelta(hours=i/TIMESTEPS_PER_HOUR) for i in range(len(df))]
        df.set_index('datetime', inplace=True)
        print(f"Using legacy datetime construction")

print(f"Date range: {df.index.min()} to {df.index.max()}")

Using datetime from simulation
Date range: 2024-07-01 00:11:00 to 2024-07-08 00:00:00


## Select Date Range for Plotting

In [11]:
# Specify the date range to plot (modify as needed)
# The dates will now match the weather file year (e.g., 2007)
PLOT_START = df.index.min().strftime('%Y-%m-%d')  # Auto-detect start
PLOT_END = df.index.max().strftime('%Y-%m-%d')    # Auto-detect end

# Or manually specify:
# PLOT_START = '2007-07-01'
# PLOT_END = '2007-07-07'

# Filter data
df_plot = df.loc[PLOT_START:PLOT_END].copy()
print(f"Plotting {len(df_plot)} timesteps from {PLOT_START} to {PLOT_END}")

Plotting 2016 timesteps from 2024-07-01 to 2024-07-08


## Plot 1: Energy Consumption

In [ ]:
# Get zone temperature columns
zone_cols = [col for col in df_plot.columns if col.startswith('zone_temp_')]
zone_names = [col.replace('zone_temp_', '').replace('_C', '') for col in zone_cols]

# Configure number of columns for subplot grid
NUM_COLS = 3  # <-- Modify this to change the number of columns

# Calculate rows needed
import math
num_zones = len(zone_cols)
num_rows = math.ceil(num_zones / NUM_COLS)

# Create subplots grid with zone names as titles
fig = make_subplots(
    rows=num_rows, 
    cols=NUM_COLS,
    shared_xaxes=True,
    shared_yaxes=True,
    vertical_spacing=0.04,
    horizontal_spacing=0.03,
    subplot_titles=zone_names
)

# Add each zone to its own subplot
for i, (col, zone_name) in enumerate(zip(zone_cols, zone_names)):
    row = i // NUM_COLS + 1
    col_idx = i % NUM_COLS + 1
    
    # Zone temperature
    fig.add_trace(
        go.Scatter(x=df_plot.index, y=df_plot[col], 
                   name=zone_name, line=dict(width=1),
                   showlegend=False),
        row=row, col=col_idx
    )
    
    # Cooling setpoint (dashed blue)
    fig.add_trace(
        go.Scatter(x=df_plot.index, y=df_plot['cooling_setpoint_C'],
                   name='Cooling SP', line=dict(color='blue', dash='dot', width=1),
                   showlegend=False),
        row=row, col=col_idx
    )
    
    # Heating setpoint (dashed red)
    fig.add_trace(
        go.Scatter(x=df_plot.index, y=df_plot['heating_setpoint_C'],
                   name='Heating SP', line=dict(color='red', dash='dot', width=1),
                   showlegend=False),
        row=row, col=col_idx
    )

# Update subplot titles to be more prominent
for i, annotation in enumerate(fig.layout.annotations):
    if i < num_zones:
        annotation.update(font=dict(size=10, color='black'))

fig.update_layout(
    height=180 * num_rows,
    title_text='Zone Temperatures by Zone (with Setpoints)',
    hovermode='x unified',
    showlegend=False,
    margin=dict(r=150, t=50, b=30),
    # Add legend annotation at right side
    annotations=list(fig.layout.annotations) + [
        dict(text="<b>—</b> Zone Temp<br><span style='color:blue'><b>···</b></span> Cooling SP<br><span style='color:red'><b>···</b></span> Heating SP",
             xref="paper", yref="paper", x=1.02, y=0.5,
             showarrow=False, font=dict(size=11), align='left',
             xanchor='left', yanchor='middle')
    ]
)

# Update y-axis labels
fig.update_yaxes(title_text='°C', col=1)

fig.show()

## Plot 2: Outdoor Temperature vs Setpoints

In [ ]:
fig = go.Figure()

# Outdoor temperature
fig.add_trace(go.Scatter(
    x=df_plot.index, y=df_plot['outdoor_temp_C'],
    name='Outdoor Temp', line=dict(color='orange', width=2)
))

# Cooling setpoint
fig.add_trace(go.Scatter(
    x=df_plot.index, y=df_plot['cooling_setpoint_C'],
    name='Cooling Setpoint', line=dict(color='blue', dash='dash')
))

# Heating setpoint
fig.add_trace(go.Scatter(
    x=df_plot.index, y=df_plot['heating_setpoint_C'],
    name='Heating Setpoint', line=dict(color='red', dash='dash')
))

fig.update_layout(
    title='Outdoor Temperature and Control Setpoints',
    xaxis_title='Date/Time',
    yaxis_title='Temperature (°C)',
    hovermode='x unified',
    legend=dict(yanchor='top', y=0.99, xanchor='left', x=0.01)
)
fig.show()

## Plot 3: Zone Temperatures

In [ ]:
# Get zone temperature columns
zone_cols = [col for col in df_plot.columns if col.startswith('zone_temp_')]
zone_names = [col.replace('zone_temp_', '').replace('_C', '') for col in zone_cols]

# Configure number of columns for subplot grid
NUM_COLS = 3  # <-- Modify this to change the number of columns

# Calculate rows needed
import math
num_zones = len(zone_cols)
num_rows = math.ceil(num_zones / NUM_COLS)

# Create subplots grid with zone names as titles
fig = make_subplots(
    rows=num_rows, 
    cols=NUM_COLS,
    shared_xaxes=True,
    shared_yaxes=True,
    vertical_spacing=0.08,
    horizontal_spacing=0.05,
    subplot_titles=zone_names
)

# Add each zone to its own subplot
for i, (col, zone_name) in enumerate(zip(zone_cols, zone_names)):
    row = i // NUM_COLS + 1
    col_idx = i % NUM_COLS + 1
    
    # Zone temperature
    fig.add_trace(
        go.Scatter(x=df_plot.index, y=df_plot[col], 
                   name=zone_name, line=dict(width=1),
                   showlegend=False),
        row=row, col=col_idx
    )
    
    # Cooling setpoint (dashed blue)
    fig.add_trace(
        go.Scatter(x=df_plot.index, y=df_plot['cooling_setpoint_C'],
                   name='Cooling SP', line=dict(color='blue', dash='dot', width=1),
                   showlegend=False),
        row=row, col=col_idx
    )
    
    # Heating setpoint (dashed red)
    fig.add_trace(
        go.Scatter(x=df_plot.index, y=df_plot['heating_setpoint_C'],
                   name='Heating SP', line=dict(color='red', dash='dot', width=1),
                   showlegend=False),
        row=row, col=col_idx
    )

# Update subplot titles to be more prominent
for i, annotation in enumerate(fig.layout.annotations):
    if i < num_zones:
        annotation.update(font=dict(size=11, color='black'), y=annotation.y + 0.01)

fig.update_layout(
    height=250 * num_rows,
    title_text='Zone Temperatures by Zone (with Setpoints)',
    hovermode='x unified',
    showlegend=False,
    # Add legend annotation at top
    annotations=list(fig.layout.annotations) + [
        dict(text="<b>—</b> Zone Temp  <b style='color:blue'>···</b> Cooling SP  <b style='color:red'>···</b> Heating SP",
             xref="paper", yref="paper", x=0.5, y=1.02,
             showarrow=False, font=dict(size=12))
    ]
)

# Update y-axis labels
fig.update_yaxes(title_text='°C', col=1)

fig.show()

## Plot 4: Combined Dashboard

In [ ]:
# Create subplots
fig = make_subplots(
    rows=3, cols=1,
    shared_xaxes=True,
    vertical_spacing=0.08,
    subplot_titles=('Power Consumption (kW)', 'Outdoor Temperature (°C)', 'Average Zone Temperature (°C)')
)

# Power consumption
fig.add_trace(
    go.Scatter(x=df_plot.index, y=df_plot['total_power_kW'], 
               name='Power', line=dict(color='green')),
    row=1, col=1
)

# Outdoor temperature
fig.add_trace(
    go.Scatter(x=df_plot.index, y=df_plot['outdoor_temp_C'], 
               name='Outdoor Temp', line=dict(color='orange')),
    row=2, col=1
)

# Average zone temperature
zone_cols = [col for col in df_plot.columns if col.startswith('zone_temp_')]
df_plot['avg_zone_temp'] = df_plot[zone_cols].mean(axis=1)

fig.add_trace(
    go.Scatter(x=df_plot.index, y=df_plot['avg_zone_temp'], 
               name='Avg Zone Temp', line=dict(color='purple')),
    row=3, col=1
)
fig.add_trace(
    go.Scatter(x=df_plot.index, y=df_plot['cooling_setpoint_C'], 
               name='Cooling SP', line=dict(color='blue', dash='dash')),
    row=3, col=1
)
fig.add_trace(
    go.Scatter(x=df_plot.index, y=df_plot['heating_setpoint_C'], 
               name='Heating SP', line=dict(color='red', dash='dash')),
    row=3, col=1
)

fig.update_layout(
    height=800,
    title_text='EnergyPlus Simulation Dashboard',
    hovermode='x unified',
    showlegend=True
)
fig.show()

## Summary Statistics

In [ ]:
# Calculate summary statistics
print("=" * 50)
print("SIMULATION SUMMARY")
print("=" * 50)
print(f"\nDate Range: {df_plot.index.min()} to {df_plot.index.max()}")
print(f"Total Timesteps: {len(df_plot)}")
print(f"\nPower Consumption:")
print(f"  Min:  {df_plot['total_power_kW'].min():,.1f} kW")
print(f"  Max:  {df_plot['total_power_kW'].max():,.1f} kW")
print(f"  Mean: {df_plot['total_power_kW'].mean():,.1f} kW")
print(f"  Total Energy: {df_plot['total_power_kW'].sum() / TIMESTEPS_PER_HOUR:,.1f} kWh")
print(f"\nOutdoor Temperature:")
print(f"  Min:  {df_plot['outdoor_temp_C'].min():.1f} °C")
print(f"  Max:  {df_plot['outdoor_temp_C'].max():.1f} °C")
print(f"  Mean: {df_plot['outdoor_temp_C'].mean():.1f} °C")
print(f"\nSetpoint Ranges:")
print(f"  Cooling: {df_plot['cooling_setpoint_C'].min():.1f} - {df_plot['cooling_setpoint_C'].max():.1f} °C")
print(f"  Heating: {df_plot['heating_setpoint_C'].min():.1f} - {df_plot['heating_setpoint_C'].max():.1f} °C")